In [ ]:
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import logging
import uuid
from pathlib import Path
from datetime import datetime, timedelta
from typing import Optional, Dict, List, Tuple
from client import LocalLLMClient, create_client
from news_function import analyze_news_single  # 复用单条分析函数


# --------------------------
# 1. 基础配置
# --------------------------
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - 批量拆分分析 - %(levelname)s - %(message)s',
    handlers=[
        logging.FileHandler("batch_split_analysis.log", encoding='utf-8'),
        logging.StreamHandler()
    ]
)
logger = logging.getLogger(__name__)

# 结果存储目录（自动创建）
OUTPUT_DIR = Path("batch_split_results")
OUTPUT_DIR.mkdir(exist_ok=True)


# --------------------------
# 2. 工具函数：写入或追加数据到Parquet文件
# --------------------------
def write_or_append_parquet(df: pd.DataFrame, file_path: str):
    """
    将DataFrame写入Parquet文件，如文件已存在则追加
    
    参数：
    - df: 要写入或追加的数据
    - file_path: 目标Parquet文件路径
    """
    table = pa.Table.from_pandas(df)
    
    # 如果文件不存在，创建新文件；否则追加
    if not Path(file_path).exists():
        pq.write_table(table, file_path)
    else:
        # 读取现有schema并追加
        existing_table = pq.read_table(file_path)
        with pq.ParquetWriter(file_path, existing_table.schema) as writer:
            writer.write_table(table)


# --------------------------
# 3. 核心函数：生成双表数据（单日结果）
# --------------------------
def _process_daily_results(daily_results: List[Dict]) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """处理单日结果，生成行业裁决表和个股推荐表的DataFrame"""
    industry_records: List[Dict] = []
    stock_records: List[Dict] = []

    for result in daily_results:
        # 基础元数据
        base_meta = {
            "original_news_id": result["original_news_id"],
            "original_news_date": result["original_news_date"],
            "original_news_title": result["original_news_title"],
            "analysis_status": result["status"],
            "error_msg": result["error_msg"],
            "log_path": result["log_path"],
            "analysis_time": result["analysis_batch_time"]
        }

        # 处理分析失败的记录
        if result["status"] == "failed":
            industry_records.append({
                **base_meta,
                "analysis_id": f"ana_{uuid.uuid4().hex[:8]}",
                "industry": "",
                "impact_direction": "",
                "confidence_score": 0,
                "comprehensive_reason": ""
            })
            continue

        # 处理分析成功的记录
        for industry in result["ruled_industries"]:
            current_analysis_id = f"ana_{uuid.uuid4().hex[:8]}"

            # 行业裁决主表记录
            industry_records.append({
                **base_meta,
                "analysis_id": current_analysis_id,
                "industry": industry.get("industry", ""),
                "impact_direction": industry.get("impact", ""),
                "confidence_score": industry.get("confidence", 0),
                "comprehensive_reason": industry.get("comprehensive_reason", "")
            })

            # 个股推荐副表记录
            for rank, stock in enumerate(industry.get("stocks", []), 1):
                stock_records.append({
                    "analysis_id": current_analysis_id,
                    "stock_name": stock.get("name", ""),
                    "stock_code": stock.get("code", ""),
                    "recommendation_reason": stock.get("reason", ""),
                    "stock_rank": rank
                })

    # 转换为DataFrame并调整字段顺序
    industry_df = pd.DataFrame(industry_records)[[
        "analysis_id", "original_news_id", "original_news_date", "original_news_title",
        "industry", "impact_direction", "confidence_score", "comprehensive_reason",
        "analysis_status", "error_msg", "log_path", "analysis_time"
    ]]

    stock_df = pd.DataFrame(stock_records)[[
        "analysis_id", "stock_name", "stock_code", "recommendation_reason", "stock_rank"
    ]]

    return industry_df, stock_df


# --------------------------
# 4. 批量分析主函数（按日期保存）
# --------------------------
def batch_analyze_split_parquet(
    input_parquet: str,
    news_date: str,
    debate_rounds: int = 2,
    llm_client: Optional[LocalLLMClient] = None,** llm_kwargs
) -> Tuple[str, str]:
    """
    批量分析Parquet新闻，按日期完成后统一保存结果
    
    参数：
    - input_parquet: 输入新闻Parquet路径
    - news_date: 新闻日期
    - debate_rounds: 辩论轮次
    - llm_client: 已实例化的LLM客户端
    - **llm_kwargs: 创建LLM客户端的参数
    
    返回：
    - 行业裁决表路径, 个股推荐表路径
    """
    # 1. 初始化LLM客户端
    if not llm_client:
        try:
            llm_client = create_client(** llm_kwargs)
            logger.info("LLM客户端初始化成功")
        except Exception as e:
            raise Exception(f"LLM客户端初始化失败：{str(e)}")

    # 2. 读取并处理输入Parquet
    try:
        logger.info(f"读取输入Parquet：{input_parquet}")
        input_df = pd.read_parquet(input_parquet)
        required_cols = ["id", "date", "title", "content"]
        missing_cols = [col for col in required_cols if col not in input_df.columns]
        if missing_cols:
            raise Exception(f"输入缺少字段：{', '.join(missing_cols)}")
        
        # 筛选出指定日期的新闻并排序
        input_df_filtered = input_df[input_df["date"] == news_date].sort_values(by="id", ascending=True).reset_index(drop=True)
        total_news = len(input_df_filtered)
        logger.info(f"读取 {total_news} 条 {news_date} 的新闻")
    except Exception as e:
        raise Exception(f"读取输入失败：{str(e)}")

    # 如果当天没有新闻，直接返回空路径
    if total_news == 0:
        logger.info(f"{news_date} 没有新闻需要分析")
        return "", ""

    # 3. 准备输出文件路径（带日期标识）
    date_suffix = news_date.replace("-", "")
    industry_path = OUTPUT_DIR / f"industry_verdict_{date_suffix}.parquet"
    stock_path = OUTPUT_DIR / f"stock_recommendation_{date_suffix}.parquet"
    
    # 4. 处理当日所有新闻
    daily_results: List[Dict] = []
    processed_count = 0

    for idx, row in input_df_filtered.iterrows():
        news_id = str(row["id"])
        logger.info(f"分析第 {idx+1}/{total_news} 条新闻（ID：{news_id}）")
        
        # 调用单条分析函数
        single_result = analyze_news_single(
            news_title=str(row["title"]),
            news_content=str(row["content"]),
            debate_rounds=debate_rounds,
            llm_client=llm_client
        )

        # 补充原始新闻元数据
        single_result.update({
            "original_news_id": news_id,
            "original_news_date": str(row["date"]),
            "original_news_title": str(row["title"]),
            "analysis_batch_time": datetime.now().strftime("%Y-%m-%d %H:%M:%S")
        })
        daily_results.append(single_result)
        processed_count += 1

    # 5. 当日新闻分析完成后，统一保存结果
    logger.info(f"{news_date} 新闻分析完成，共处理 {processed_count} 条，开始保存结果...")
    
    # 处理当日结果
    daily_industry_df, daily_stock_df = _process_daily_results(daily_results)
    
    # 保存结果（如文件已存在则追加）
    write_or_append_parquet(daily_industry_df, str(industry_path))
    write_or_append_parquet(daily_stock_df, str(stock_path))
    
    logger.info(f"{news_date} 结果保存完成，行业裁决表：{industry_path}，个股推荐表：{stock_path}")

    return str(industry_path), str(stock_path)


# --------------------------
# 5. 使用示例
# --------------------------
if __name__ == "__main__":
    # 配置参数
    INPUT_PARQUET = "../data/stock_daily_cctvnews.parquet"  # 输入新闻路径
    DEBATE_ROUNDS = 2  # 辩论轮次
    LLM_KWARGS = {
        # "model": "gpt-4-turbo",  # 实际使用时填写LLM参数
        # "api_key": "your_api_key"
    }

    # 获取20250101至今以来的日期列表，形成yyyy-mm-dd的格式
    start_date = datetime(2025, 1, 1)
    end_date = datetime.now()
    date_list = [start_date + timedelta(days=x) for x in range((end_date - start_date).days + 1)]
    date_list = [date.strftime("%Y-%m-%d") for date in date_list]

    # 依次遍历date_list ，对每个日期进行分析
    for news_date in date_list:
        try:
            # 执行批量拆分分析
            industry_table_path, stock_table_path = batch_analyze_split_parquet(
                input_parquet=INPUT_PARQUET,
                news_date=news_date,
                debate_rounds=DEBATE_ROUNDS,** LLM_KWARGS
            )
            
            if industry_table_path and stock_table_path:
                # 打印结果
                print("="*70)
                print(f"{news_date} 分析完成！")
                print(f"输入文件：{INPUT_PARQUET}")
                print(f"行业裁决表：{industry_table_path}")
                print(f"个股推荐表：{stock_table_path}")
                print(f"提示：可通过 'analysis_id' 字段关联两张表")
                print("="*70)
        except Exception as e:
            print(f"{news_date} 分析失败：{str(e)}")
            logger.error(f"{news_date} 分析失败：{str(e)}")


2025-10-11 20:48:44,977 - INFO - LLM客户端初始化成功
2025-10-11 20:48:44,991 - INFO - 读取输入Parquet：../data/stock_daily_cctvnews.parquet
2025-10-11 20:48:46,849 - INFO - 读取 12 条 2025-01-01 的新闻
2025-10-11 20:48:46,866 - INFO - 分析第 1/12 条新闻（ID：114300）
2025-10-11 20:48:46,867 - INFO - 开始分析单条新闻（ID：news_single_20251011204846_212，标题：《求是》杂志发表习近平总书记重要文章《以中国式现代化全面推进...）
2025-10-11 20:48:46,870 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-11 20:48:46,872 - INFO - 用户消息: 标题：《求是》杂志发表习近平总书记重要文章《以中国式现代化全面推进强国建设、民族复兴伟业》
内容：央视网消息
（新闻联播）：2025年1月1日出版的第1期《求是》杂志发表中共中央总书记、国家主席、中央军委主席习近平的重要文章《以中国式现代化全面推进强国建设、民族复兴伟业》。
文章强调，概括提出并深入阐述中国式现代化理论，是党的二十大的一个重大理论创新，是科学社会主义的最新重大成果。
文章指出，中国式现代化是我们党领导人民长期探索和实践的重大成果。党的十八大以来，我们党在已有基础上继续前进，坚持问题导向，围绕解决现代化建设中存在的突出矛盾和问题，全面深化改革，不断实现理论和实践上的创新突破，成功推进和拓展了中国式现代化。我们在认识上不断深化，在战略上不断完善，在实践上不断丰富，推动党和国家事业取得历史性成就、发生历史性变革，为中国式现代化提供了更为完善的制度保证、更为坚实的物质基础、更为主动的精神力量。
文章指出，党的领导直接关系中国式现代化的根本方向、前途命运、最终成败。党的二十大报告明确指出：“中国式现代化，是中国共产党领导的社会主义现代化”。这是对中国式现代化定性的话，是管总、管根本的。党的领导决定中国式现代化的根本性质。党的领导确保中国式现代化

2025-01-01 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250101.parquet
个股推荐表：batch_split_results\stock_recommendation_20250101.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-11 20:54:51,418 - INFO - 响应内容: {"positive": []}...
2025-10-11 20:54:51,419 - INFO - 响应时间: 1796.87毫秒
2025-10-11 20:54:51,422 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-11 20:54:51,423 - INFO - 用户消息: 正方首次观点：{"positive": []}
新闻内容：标题：习近平和夫人彭丽媛向美国华盛顿州中学师生代表回赠新年贺卡
内容：央视网消息
（新闻联播）：1月1日，国家主席习近平和夫人彭丽媛向美国华盛顿州中学师生代表回赠新年贺卡，致以新年祝福，表示2025年是中国人民抗日战争和世界反法西斯战争胜利80周年。第二次世界大战期间，中美共同为和平和正义而战，两国人民的友谊经受了血与火的考验，历久弥新。希望中美两国青少年继续积极参与“未来5年邀请5万名美国青少年来华交流学习”倡议，加强交流互动，增进相互了解，传承传统友谊，为推动中美关系发展、促进世界和平贡献力量。
此前，美国华盛顿州美中青少年学生交流协会和林肯中学、体育场中学曾参加“5年5万”倡议访华的师生代表向习近平主席夫妇和全中国人民致新年贺卡，100多位老师和同学在贺卡上签名。师生们在贺卡上用中文书写：“纪念抗战胜利80周年，纪念世界反法西斯战争胜利80周年。喜迎新年，和平万岁，中美友谊长存！
请针对正方观点进行驳斥并提出利空
2025-10-11 20:54:51,424 - INFO - 参数: {'temperature': 0.4, 'max_tokens': 20000}
2025-10-11 20:54:53,608 - INFO - 响应内容: {"negative": [], "refute": "该新闻为外交礼仪性互动，不构成实质性经济利好，对相关行业无直接推动作用，难以支撑市场炒作逻辑。"}...
2025-10-11 20:54:53,609 - INFO - 响应时间: 2187.11毫秒
2025-10-11 20:54:53,611 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-11 2

2025-01-02 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250102.parquet
个股推荐表：batch_split_results\stock_recommendation_20250102.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-11 21:01:07,275 - INFO - 响应内容: {"positive": []}...
2025-10-11 21:01:07,276 - INFO - 响应时间: 1676.52毫秒
2025-10-11 21:01:07,277 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-11 21:01:07,279 - INFO - 用户消息: 正方首次观点：{"positive": []}
新闻内容：标题：习近平致电祝贺卡韦拉什维利就任格鲁吉亚总统
内容：央视网消息
（新闻联播）：近日，国家主席习近平致电米哈伊尔·卡韦拉什维利，祝贺他就任格鲁吉亚总统。

习近平指出，当前中格战略伙伴关系保持积极发展势头。双方政治互信持续巩固，共建“一带一路”合作成果丰硕，国际协作富有成效。我高度重视中格关系发展，愿同总统先生一道努力，赓续两国传统友谊，深化双方互利合作，推动中格关系取得更大发展，更好造福两国人民。
请针对正方观点进行驳斥并提出利空
2025-10-11 21:01:07,280 - INFO - 参数: {'temperature': 0.4, 'max_tokens': 20000}
2025-10-11 21:01:09,699 - INFO - 响应内容: {"negative": [], "refute": "该新闻为外交表态，属地缘政治利好，但对A股相关行业无实质影响，难以形成可交易的政策或业绩驱动，不具备投资逻辑。"}...
2025-10-11 21:01:09,700 - INFO - 响应时间: 2422.19毫秒
2025-10-11 21:01:09,701 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-11 21:01:09,702 - INFO - 用户消息: 之前的辩论内容：{"pro_initial": {"positive": []}, "anti_initial": {"negative": [], "refute": "该新闻为外交表态，属地缘政治利好，但对A股相关行业无实质影响，难以形成可交易的政策或业绩驱动，不具备投资逻辑。"}}
新闻内容：标题：习近平致电祝贺卡

...

2025-10-12 00:24:29,954 - INFO - 读取 13 条 2025-01-26 的新闻
2025-10-12 00:24:29,972 - INFO - 分析第 1/13 条新闻（ID：114642）
2025-10-12 00:24:29,974 - INFO - 开始分析单条新闻（ID：news_single_20251012002429_936，标题：中央领导同志看望老同志...）
2025-10-12 00:24:29,975 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-12 00:24:29,977 - INFO - 用户消息: 标题：中央领导同志看望老同志
内容：央视网消息
（新闻联播）：春节前夕，中共中央总书记、国家主席、中央军委主席习近平等党和国家领导人分别看望或委托有关方面负责同志看望了胡锦涛、朱镕基、李瑞环、温家宝、贾庆林、张德江、俞正声、栗战书、汪洋、宋平、李岚清、曾庆红、吴官正、李长春、罗干、贺国强、刘云山、王岐山、张高丽和田纪云、迟浩田、王乐泉、王兆国、回良玉、刘淇、吴仪、曹刚川、曾培炎、王刚、刘延东、李源潮、马凯、许其亮、孙春兰、李建国、范长龙、孟建柱、郭金龙、王晨、刘鹤、杨洁篪、杨晓渡、陈全国、郭声琨、王汉斌、何勇、杜青林、赵洪祝、尤权、王丙乾、邹家华、彭珮云、李铁映、许嘉璐、蒋正华、顾秀莲、热地、盛华仁、路甬祥、华建敏、陈至立、司马义·铁力瓦尔地、蒋树声、王胜俊、陈昌智、严隽琪、张平、向巴平措、张宝文、曹建明、张春贤、吉炳轩、艾力更·依明巴海、万鄂湘、陈竺、白玛赤林、唐家璇、戴秉国、常万全、赵克志、韩杼滨、贾春旺、宋健、胡启立、王忠禹、李贵鲜、郝建秀、徐匡迪、张怀西、李蒙、廖晖、白立忱、陈奎元、阿不来提·阿不都热西提、李兆焯、黄孟复、张梅颖、张榕明、钱运录、孙家正、李金华、郑万通、邓朴方、厉无畏、陈宗兴、王志珍、韩启德、林文漪、罗富和、李海峰、陈元、周小川、王家瑞、齐续春、马培华、刘晓峰、王钦敏、张庆黎、刘奇葆、董建华、万钢、卢展工、王正伟、马飚、陈晓光、杨传堂、李斌、汪永清、辜胜阻、刘新成等老同志，向他们致以诚挚的节日问候，衷心祝愿他们新春愉快、健康长寿。
老同志们对此表示感谢，高度评价党中央过去一年的工作，对习近平总书记作为党中央的核心

2025-01-26 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250126.parquet
个股推荐表：batch_split_results\stock_recommendation_20250126.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-12 00:34:06,233 - INFO - 响应内容: {"positive": []}...
2025-10-12 00:34:06,235 - INFO - 响应时间: 3089.43毫秒
2025-10-12 00:34:06,235 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-12 00:34:06,237 - INFO - 用户消息: 正方首次观点：{"positive": []}
新闻内容：标题：中共中央国务院举行春节团拜会 习近平发表讲话 代表党中央和国务院 向全国各族人民 向香港特别行政区同胞 澳门特别行政区同胞 台湾同胞和海外侨胞拜年
内容：央视网消息
（新闻联播）：中共中央、国务院27日上午在人民大会堂举行2025年春节团拜会。中共中央总书记、国家主席、中央军委主席习近平发表讲话，代表党中央和国务院，向全国各族人民，向香港特别行政区同胞、澳门特别行政区同胞、台湾同胞和海外侨胞拜年。

习近平强调，即将过去的甲辰龙年，是我们振奋龙马精神、历经风雨彩虹的一年。一年来，面对复杂严峻形势，我们沉着应变、综合施策，攻坚克难、砥砺奋进，中国式现代化迈出新的坚实步伐。

李强主持团拜会，赵乐际、王沪宁、蔡奇、丁薛祥、李希、韩正等出席。

人民大会堂宴会厅灯光璀璨、暖意融融，各界人士2000多人欢聚一堂、共迎佳节，现场洋溢着欢乐祥和的节日气氛。

上午10时许，在欢快的乐曲声中，习近平等党和国家领导人步入大厅，向大家亲切致意，同大家互致问候、祝福新春，全场响起热烈掌声。

习近平在讲话中指出，过去一年，我们扎实推动高质量发展，有效落实各项存量政策，加力推出一揽子增量政策，促进经济回暖向好。科技创新和产业创新成果丰硕，新质生产力稳步发展。区域协调发展、城乡融合发展展现新面貌。放眼全球，我国仍然是世界经济增长的重要引擎。我们注重各项事业协调并进，社会主义民主法治建设、文化建设、社会建设、生态文明建设、国防和军队建设都取得新进步。隆重庆祝新中国成立75周年。召开党的二十届三中全会，推动进一步全面深化改革。着力保障和改善民生，就业、物价保持稳定，脱贫攻坚成果进一步巩固拓展。统筹发展和安全，有序有效化解重点领域风险，社会大局保持稳定。有力应对重大自然灾害，高效开展西藏定日高寒缺氧

2025-01-27 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250127.parquet
个股推荐表：batch_split_results\stock_recommendation_20250127.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-12 00:44:17,935 - INFO - 读取 12 条 2025-01-28 的新闻
2025-10-12 00:44:17,937 - INFO - 分析第 1/12 条新闻（ID：114670）
2025-10-12 00:44:17,939 - INFO - 开始分析单条新闻（ID：news_single_20251012004417_962，标题：以蛇行千里的劲头 书写中国式现代化新篇章——习近平总书记在春...）
2025-10-12 00:44:17,941 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-12 00:44:17,944 - INFO - 用户消息: 标题：以蛇行千里的劲头 书写中国式现代化新篇章——习近平总书记在春节团拜会上的重要讲话引发热烈反响
内容：央视网消息
（新闻联播）：新春佳节到来之际，习近平总书记在二〇二五年春节团拜会上发表重要讲话，总结过去一年全国人民团结奋斗取得的扎实成绩，展望新时代新征程改革发展的目标任务，凝聚起亿万人民向着宏伟目标接续奋进的磅礴力量。总书记的重要讲话在全国各地引发热烈反响。大家表示，要更加紧密地团结在以习近平同志为核心的党中央周围，以蛇行千里的劲头，坚定信心、满怀希望，开拓进取、顽强奋斗，共同书写中国式现代化新篇章。

在昨天（1月27日）的春节团拜会上，习近平等党和国家领导人向大家亲切致意，同大家互致问候、祝福新春。

习近平总书记强调，即将过去的甲辰龙年是我们振奋龙马精神、历经风雨彩虹的一年。一年来，面对复杂严峻形势，我们沉着应变、综合施策，攻坚克难、砥砺奋进，中国式现代化迈出新的坚实步伐。总书记的重要讲话传遍大江南北、催人奋进，人们满怀信心和期待迎接新春到来。

习近平总书记指出，前进道路上，只要我们坚定信念信心不动摇，直面矛盾问题不回避，应对风险挑战不退缩，就一定能够打开改革发展新天地。总书记的重要讲话激励全国人民向着宏伟目标接续奋进。 

春节期间，还有很多人在坚守岗位。在长江流域江海转运枢纽港、在大科学装置运行现场、在春运保障一线……各行各业的人们用拼搏奋斗为祖国各项事业增光添彩。

2025年是“十四五”规划收官之年。习近平总书记强调，我们要始终坚持以人民为中心，及时有效回应群众需求和关切，用心